In [1]:
import os
import time
os.environ["CUDA_LAUNCH_BLOCKING"] = "1"
from os import listdir
import pandas as pd
import numpy as np
import glob
import cv2
import json
from os.path import expanduser
import splitfolders
import shutil
from define_path import Def_Path
from datetime import datetime

from tqdm import tqdm

import torch 
import torchvision
from torchvision import models
from torchvision.models.detection.rpn import AnchorGenerator
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn 
import torchvision.transforms as T
from torchvision.transforms import functional as F
from torchsummary import summary
from sklearn.model_selection import train_test_split
from torch.cuda.amp import GradScaler, autocast

import albumentations as A # Library for augmentations

import matplotlib.pyplot as plt 
from PIL import Image

import transforms, utils, engine, train
from utils import collate_fn
from engine import train_one_epoch, evaluate

import torch
import torch.nn as nn
import torch.nn.functional as func
import numpy as np
from torch.autograd import Variable
import torch_geometric.nn as pyg
from torch_geometric.nn import SAGEConv, GCNConv, GATConv
from torch_geometric.data import Data

t = torch.cuda.get_device_properties(0).total_memory
print(t)
torch.cuda.empty_cache()

r = torch.cuda.memory_reserved(0)
print(r)
a = torch.cuda.memory_allocated(0)
print(a)
# f = r-a  # free inside reserved

weights_path = '/home/jc-merlab/Pictures/Data/trained_models/keypointsrcnn_planning_b1_e100_v4.pth'

n_nodes = 9

16899571712
0
0


In [2]:
# to generalize home directory. User can change their parent path without entering their home directory
path = Def_Path()

# parent_path =  path.home + "/Pictures/" + "Data/"

parent_path =  "/home/jc-merlab/Pictures/Data/"

# root_dir = parent_path + path.year + "-" + path.month + "-" + path.day + "/"
root_dir = parent_path + "occ_panda_physical_dataset/"

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
# torch.cuda.set_per_process_memory_fraction(0.9, 0)
print(device)

cuda


In [4]:
def train_transform():
    return A.Compose([
        A.Sequential([
            A.RandomRotate90(p=1), # Random rotation of an image by 90 degrees zero or more times
            A.RandomBrightnessContrast(brightness_limit=0.2, contrast_limit=0.3, brightness_by_max=True, always_apply=False, p=1), # Random change of brightness & contrast
        ], p=1)
#         A.Resize(640, 480)  # Resize all images to be 640x480
    ],
    keypoint_params=A.KeypointParams(format='xy'), # More about keypoint formats used in albumentations library read at https://albumentations.ai/docs/getting_started/keypoints_augmentation/
    bbox_params=A.BboxParams(format='pascal_voc', label_fields=['bboxes_labels']) # Bboxes should have labels, read more at https://albumentations.ai/docs/getting_started/bounding_boxes_augmentation/
    )

In [5]:
def train_test_split(src_dir):
    dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_img) and os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_img)
        os.mkdir(dst_dir_anno)
        
    for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
        shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = parent_path + "split_folder_output" + "-" + path.year + "-" + path.month + "-" + path.day 
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(0.95, 0.025, 0.025), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
    shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  

In [6]:
class KPDataset(Dataset):
    def __init__(self, root, transform=None, demo=False):                
        self.root = root
        self.transform = transform
        self.demo = demo # Use demo=True if you need transformed and original images (for example, for visualization purposes)
        self.imgs_files = sorted(os.listdir(os.path.join(root, "images")))
        self.annotations_files = sorted(os.listdir(os.path.join(root, "annotations")))
    
    def __getitem__(self, idx):
        img_file = self.imgs_files[idx]
        img_path = os.path.join(self.root, "images", self.imgs_files[idx])
        annotations_path = os.path.join(self.root, "annotations", self.annotations_files[idx])

        img_original = cv2.imread(img_path)
        img_original = cv2.cvtColor(img_original, cv2.COLOR_BGR2RGB)
        
        with open(annotations_path) as f:
            data = json.load(f)
            bboxes_original = data['bboxes']
            keypoints_original = data['keypoints']
            
            # All objects are keypoints on the robot
            bboxes_labels_original = [] 
            bboxes_labels_original.append('base_joint')
            bboxes_labels_original.append('joint2')
            bboxes_labels_original.append('joint3')
            bboxes_labels_original.append('joint4')
            bboxes_labels_original.append('joint5')
            bboxes_labels_original.append('joint6')  
            bboxes_labels_original.append('joint7')
            bboxes_labels_original.append('joint8')
            bboxes_labels_original.append('joint9')

        if self.transform:   
            # Converting keypoints from [x,y,visibility]-format to [x, y]-format + Flattening nested list of keypoints            
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]], where each keypoint is in [x, y]-format            
            # Then we need to convert it to the following list:
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2]
            keypoints_original_flattened = [el[0:2] for kp in keypoints_original for el in kp]
            
            # Apply augmentations
            transformed = self.transform(image=img_original, bboxes=bboxes_original, bboxes_labels=bboxes_labels_original, keypoints=keypoints_original_flattened)
            img = transformed['image']
            bboxes = transformed['bboxes']
            # Unflattening list transformed['keypoints']
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2], where each keypoint is in [x, y]-format
            # Then we need to convert it to the following list:
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]]
            keypoints_transformed_unflattened = np.reshape(np.array(transformed['keypoints']), (-1,1,2)).tolist()

            # Converting transformed keypoints from [x, y]-format to [x,y,visibility]-format by appending original visibilities to transformed coordinates of keypoints
            keypoints = []
            for o_idx, obj in enumerate(keypoints_transformed_unflattened):
#                 print("object", obj)
#                 print(" obj index", o_idx)# Iterating over objects
                obj_keypoints = []
                for k_idx, kp in enumerate(obj): # Iterating over keypoints in each object
                    obj_keypoints.append(kp + [keypoints_original[o_idx][k_idx][2]])
                keypoints.append(obj_keypoints)
        
        else:
            img, bboxes, keypoints = img_original, bboxes_original, keypoints_original        
        
        # Convert everything into a torch tensor        
        bboxes = torch.as_tensor(bboxes, dtype=torch.float32)       
        target = {}
        labels = [1, 2, 3, 4, 5, 6, 7, 8, 9]  
#         labels = [1, 2, 3, 4, 5, 6]
        target["boxes"] = bboxes
        target["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are joint positions
        target["image_id"] = torch.tensor([idx])
        target["area"] = (bboxes[:, 3] - bboxes[:, 1]) * (bboxes[:, 2] - bboxes[:, 0])
        target["iscrowd"] = torch.zeros(len(bboxes), dtype=torch.int64)
        target["keypoints"] = torch.as_tensor(keypoints, dtype=torch.float32)
        img = F.to_tensor(img)        
        bboxes_original = torch.as_tensor(bboxes_original, dtype=torch.float32)
        target_original = {}
        target_original["boxes"] = bboxes_original
        target_original["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are glue tubes
        target_original["image_id"] = torch.tensor([idx])
        target_original["area"] = (bboxes_original[:, 3] - bboxes_original[:, 1]) * (bboxes_original[:, 2] - bboxes_original[:, 0])
        target_original["iscrowd"] = torch.zeros(len(bboxes_original), dtype=torch.int64)
        target_original["keypoints"] = torch.as_tensor(keypoints_original, dtype=torch.float32)        
        img_original = F.to_tensor(img_original)

        if self.demo:
            return img, target, img_original, target_original, img_file
        else:
            return img, target, img_file
    
    def __len__(self):
        return len(self.imgs_files)

In [7]:
class GraphEncoder(nn.Module):
    def __init__(self, in_channels, hidden_channels):
        super(GraphEncoder, self).__init__()
        self.conv1 = GCNConv(in_channels, hidden_channels)
        self.conv2 = GCNConv(hidden_channels, hidden_channels)
        self.conv3 = GCNConv(hidden_channels, hidden_channels)        

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index)
        x = torch.nn.functional.relu(x)
        x = torch.nn.functional.dropout(x, p=0.5, training=self.training)
        x = self.conv2(x, edge_index)
        x = torch.nn.functional.relu(x)
        x = torch.nn.functional.dropout(x, p=0.5, training=self.training)
        x = self.conv3(x, edge_index) 
        
        return x
    
class GraphDecoder(nn.Module):
    def __init__(self, hidden_channels, out_channels):
        super(GraphDecoder, self).__init__()
        self.conv1 = GCNConv(hidden_channels, hidden_channels)
        self.conv2 = GCNConv(hidden_channels, hidden_channels)
        self.conv3 = GCNConv(hidden_channels, out_channels)

    def forward(self, z, edge_index):
        z = self.conv1(z, edge_index)
        z = torch.nn.functional.relu(z)
        z = torch.nn.functional.dropout(z, p=0.5, training=self.training)
        z = self.conv2(z, edge_index)
        z = torch.nn.functional.relu(z)
        z = torch.nn.functional.dropout(z, p=0.5, training=self.training)
        z = self.conv3(z, edge_index)
        
        return z
    

class GraphAutoencoder(nn.Module):
    def __init__(self, encoder, decoder):
        super(GraphAutoencoder, self).__init__()
        self.encoder = encoder
        self.decoder = decoder

    def forward(self, x, edge_index):
        z = self.encoder(x, edge_index)
        x_hat = self.decoder(z, edge_index)
        return x_hat, z

In [8]:
def calculate_distance_angle(kp1, kp2):
    dx = kp2[0] - kp1[0]
    dy = kp2[1] - kp1[1]
    dx, dy = torch.tensor(dx).to(device), torch.tensor(dy).to(device)
    distance = torch.sqrt(dx ** 2 + dy ** 2)
    angle = torch.atan2(dy, dx)
    return distance, angle

def calculate_gt_distances_angles(keypoints_gt):
#     print(f"keypoints_gt shape: {keypoints_gt.shape}")  # Debug print
    batch_size, num_keypoints, num_dims = keypoints_gt.shape
    assert num_keypoints == n_nodes and num_dims == 2, "keypoints_gt must have shape (batch_size, 9, 2)"
    distances_angles = []

    for b in range(batch_size):
        batch_distances_angles = torch.zeros((num_keypoints, 4), dtype=torch.float32).to(device)  # Initialize with zeros
        
        for i in range(num_keypoints):
            current_kp = keypoints_gt[b, i]
            next_i = (i + 1) % num_keypoints
            prev_i = (i - 1 + num_keypoints) % num_keypoints

            # Calculate distance and angle to the next keypoint
            dist, angle = calculate_distance_angle(current_kp, keypoints_gt[b, next_i])
            batch_distances_angles[i, 0] = dist
            batch_distances_angles[i, 1] = angle

            # Calculate distance and angle to the previous keypoint
            dist, angle = calculate_distance_angle(current_kp, keypoints_gt[b, prev_i])
            batch_distances_angles[i, 2] = dist
            batch_distances_angles[i, 3] = angle

        distances_angles.append(batch_distances_angles)

    distances_angles = torch.stack(distances_angles)
#     print("ground truth dist and angles", distances_angles)
    return distances_angles

In [9]:
class KeypointPipeline(nn.Module):
    def __init__(self, weights_path):
        super(KeypointPipeline, self).__init__()
        self.keypoint_model = torch.load(weights_path).to(device)
        self.graph_autoencoder = GraphAutoencoder(
            encoder=GraphEncoder(8, 512),
            decoder=GraphDecoder(512, 8)
        ).to(device)
        
    def process_model_output(self, output):
        scores = output[0]['scores'].detach().cpu().numpy()
        labels = output[0]['labels'].detach().cpu().numpy()
        keypoints = output[0]['keypoints'].detach().cpu().numpy()
#         print("keypoints before post_nms", keypoints)
        high_scores_idxs = np.where(scores > 0.01)[0].tolist()
        post_nms_idxs = torchvision.ops.nms(output[0]['boxes'][high_scores_idxs], output[0]['scores'][high_scores_idxs], 0.3).cpu().numpy()
        confidence_nms = output[0]['scores'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()
        labels_nms = output[0]['labels'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()
        confidence = output[0]['scores'][high_scores_idxs].detach().cpu().numpy()
        labels =  output[0]['labels'][high_scores_idxs].detach().cpu().numpy()
        keypoints = []
#         for idx, kps in enumerate(output[0]['keypoints'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()):
#             keypoints.append(list(map(int, kps[0, 0:2])) + [confidence[idx]] + [labels[idx]])
            
        for idx, kps in enumerate(output[0]['keypoints'][high_scores_idxs].detach().cpu().numpy()):
            keypoints.append(list(map(int, kps[0, 0:2])) + [confidence[idx]] + [labels[idx]])
        
        keypoints = [torch.tensor(kp, dtype=torch.float32).to(device) if not isinstance(kp, torch.Tensor) else kp for kp in keypoints]
        keypoints = torch.stack(keypoints).to(device)
        
        unique_labels, best_keypoint_indices = torch.unique(keypoints[:, 3], return_inverse=True)
        best_scores, best_indices = torch.max(keypoints[:, 2].unsqueeze(0) * (best_keypoint_indices == torch.arange(len(unique_labels)).unsqueeze(1).cuda()), dim=1)
        keypoints = keypoints[best_indices]
        
        print("initial predicted keypoints", keypoints)
        
        return keypoints
    
    def fill_missing_keypoints(self, keypoints, image_width, image_height):
        keypoints_dict = {int(kp[3]): kp for kp in keypoints}
        complete_keypoints = []
        labels = [int(kp[3]) for kp in keypoints]
        
        # Identify missing labels
        all_labels = set(range(1, 10))
        missing_labels = list(all_labels - set(labels))
        missing_labels.sort()
        
        # Handle consecutive missing labels by placing them at the midpoint or image center
        for i in range(1, 10):
            if i in keypoints_dict:
                complete_keypoints.append(keypoints_dict[i].tolist())
            else:
                prev_label = i - 1 if i > 1 else 9
                next_label = i + 1 if i < 9 else 1
                
                prev_kp = keypoints_dict.get(prev_label, None)
                next_kp = keypoints_dict.get(next_label, None)
                
                print("Previous Kp", prev_kp)
                print("Next Kp", next_kp)

                if prev_kp is None and next_kp is None:
                    avg_x, avg_y = image_width / 2, image_height / 2
                elif prev_kp is None:
                    avg_x, avg_y = (next_kp[0] + image_width / 2) / 2, (next_kp[1] + image_height / 2) / 2
                elif next_kp is None:
                    avg_x, avg_y = (prev_kp[0] + image_width / 2) / 2, (prev_kp[1] + image_height / 2) / 2
                else:
                    avg_x = (prev_kp[0] + next_kp[0]) / 2
                    avg_y = (prev_kp[1] + next_kp[1]) / 2

                complete_keypoints.append([avg_x, avg_y, 0, i])
                print(f"Filled missing keypoint for label {i} at position ({avg_x}, {avg_y})")

                
        print("filled missing keypoints", complete_keypoints)
        
        return torch.tensor(complete_keypoints, dtype=torch.float32).to(device)

    def normalize_keypoints(self, keypoints, image_width, image_height):
        keypoints[:, 0] = (keypoints[:, 0] - image_width / 2) / (image_width / 2)
        keypoints[:, 1] = (keypoints[:, 1] - image_height / 2) / (image_height / 2)
        return keypoints
    

    def keypoints_to_graph(self, keypoints, image_width, image_height):
        node_features = []
        placeholder_mask = []
        for i, kp in enumerate(keypoints):
            x, y, conf, label = kp
            prev_kp = keypoints[i - 1]
            next_kp = keypoints[(i + 1) % len(keypoints)]
            dist_next, angle_next = calculate_distance_angle([x, y], next_kp[:2])
            dist_prev, angle_prev = calculate_distance_angle([x, y], prev_kp[:2])
            node_features.append([x, y, conf, label, dist_next, angle_next, dist_prev, angle_prev])
            placeholder_mask.append(conf == 0)  # Assuming placeholder if confidence is 0
            
        node_features = torch.tensor(node_features, dtype=torch.float32).to(device)
        placeholder_mask = torch.tensor(placeholder_mask, dtype=torch.bool).to(device)
        edge_index = torch.tensor([[i, (i + 1) % len(keypoints)] for i in range(len(keypoints))] + 
                                  [[(i + 1) % len(keypoints), i] for i in range(len(keypoints))], dtype=torch.long).t().contiguous().to(device)
        
        print(Data(x=node_features, edge_index=edge_index), placeholder_mask)
        return Data(x=node_features, edge_index=edge_index), placeholder_mask
    
    def forward(self, imgs):
        keypoint_model_training = self.keypoint_model.training
        self.keypoint_model.eval()

        with torch.no_grad():
            batch_outputs = [self.keypoint_model(img.unsqueeze(0).to(device)) for img in imgs]

        self.keypoint_model.train(mode=keypoint_model_training)

        batch_labeled_keypoints = [self.process_model_output(output) for output in batch_outputs]

        # Fill missing keypoints first and then normalize them
        for idx, keypoints in enumerate(batch_labeled_keypoints):
            image_width, image_height = 640, 480
            filled_keypoints = self.fill_missing_keypoints(keypoints, image_width, image_height)
            normalized_keypoints = self.normalize_keypoints(filled_keypoints, image_width, image_height)
            batch_labeled_keypoints[idx] = normalized_keypoints
       
        all_graphs, placeholder_masks = zip(*[self.keypoints_to_graph(keypoints, 640, 480) for keypoints in batch_labeled_keypoints])
        all_predictions, latent_reps, all_placeholder_masks = [], [], []
        for graph, placeholder_mask in zip(all_graphs, placeholder_masks):
            x_hat, z = self.graph_autoencoder(graph.x, graph.edge_index)
            all_predictions.append(x_hat)
            latent_reps.append(graph.x)
            all_placeholder_masks.append(placeholder_mask)

        final_predictions = torch.stack(all_predictions)
        latent_reps = torch.stack(latent_reps)
        placeholder_masks = torch.stack(all_placeholder_masks)
        
        return final_predictions, latent_reps, placeholder_masks

In [10]:
def reconstruction_loss(x, x_hat, placeholder_mask):
    # x final prediction
    # x_hat latent_reps, that is input for encoder
    return func.mse_loss(x_hat[~placeholder_mask], x[~placeholder_mask])


def kgnn2d_loss(gt_keypoints, pred_keypoints, gt_distances_next, gt_angles_next, gt_distances_prev, gt_angles_prev, pred_distances_next, pred_angles_next, pred_distances_prev, pred_angles_prev, x, x_hat, placeholder_mask):
    keypoints_loss = func.mse_loss(pred_keypoints, gt_keypoints)
    prev_distances_loss = func.mse_loss(pred_distances_prev, gt_distances_prev)
    prev_angles_loss = func.mse_loss(pred_angles_prev, gt_angles_prev)
    next_distances_loss = func.mse_loss(pred_distances_next, gt_distances_next)
    next_angles_loss = func.mse_loss(pred_angles_next, gt_angles_next)
    recon_loss = reconstruction_loss(x, x_hat, placeholder_mask)
    return keypoints_loss + prev_distances_loss + prev_angles_loss + next_distances_loss + next_angles_loss + recon_loss

In [11]:
def process_batch_keypoints(target_dicts):
    batch_size = len(target_dicts)
    keypoints_list = []
    for dict_ in target_dicts:
        keypoints = dict_['keypoints'].squeeze(1).to(device)
        xy_coords = keypoints[:, :2]
        keypoints_list.append(xy_coords)
    keypoints_gt = torch.stack(keypoints_list).float().cuda()
    return keypoints_gt

def reorder_batch_keypoints(batch_keypoints):    
    batch_size, num_keypoints, num_features = batch_keypoints.shape
    reordered_keypoints_batch = []
    for i in range(batch_size):
        normalized_keypoints = batch_keypoints[i]
#         print("predicted normalized keypoints for reordering")
#         print(normalized_keypoints)
        reordered_normalized_keypoints = torch.zeros(num_keypoints, 2, device=batch_keypoints.device)
        rounded_labels = torch.round(normalized_keypoints[:, 3]).int()
#         print("rounded labels", rounded_labels)
        used_indices = []
        for label in range(1, 10):
#             print("label", label)
            valid_idx = (rounded_labels == label).nonzero(as_tuple=True)[0]
#             print("valid index", valid_idx.numel())
            if valid_idx.numel() > 0:
#                 print("index in valid index is present")
                reordered_normalized_keypoints[label - 1] = normalized_keypoints[valid_idx[0], :2]
            else:
#                 print("used_indices")
#                 print("index in valid index is not present")
                invalid_idx = ((rounded_labels < 1) | (rounded_labels > 9)).nonzero(as_tuple=True)[0]
#                 print("invalid idx ", invalid_idx)
                invalid_idx = [idx for idx in invalid_idx if idx not in used_indices]
                if invalid_idx:
                    reordered_normalized_keypoints[label - 1] = normalized_keypoints[invalid_idx[0], :2]
                    used_indices.append(invalid_idx[0])
        reordered_keypoints_batch.append(reordered_normalized_keypoints)
    return torch.stack(reordered_keypoints_batch)

def denormalize_keypoints(batch_keypoints, width=640, height=480):
    denormalized_keypoints = []
    for kp in batch_keypoints:
        denormalized_x = (kp[:, 0] * (width / 2)) + (width / 2)
        denormalized_y = (kp[:, 1] * (height / 2)) + (height / 2)
        denormalized_kp = torch.stack((denormalized_x, denormalized_y), dim=1)
        denormalized_keypoints.append(denormalized_kp)
    denormalized_keypoints = torch.stack(denormalized_keypoints)
    return denormalized_keypoints

In [12]:
model = KeypointPipeline(weights_path)
model = model.to(device)

optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
scaler = GradScaler()

num_epochs = 1
batch_size = 1

split_folder_path = train_test_split(root_dir)
KEYPOINTS_FOLDER_TRAIN = split_folder_path +"/train"
KEYPOINTS_FOLDER_VAL = split_folder_path +"/val"
KEYPOINTS_FOLDER_TEST = split_folder_path +"/test"

dataset_train = KPDataset(KEYPOINTS_FOLDER_TRAIN, transform=None, demo=False)
dataset_val = KPDataset(KEYPOINTS_FOLDER_VAL, transform=None, demo=False)
dataset_test = KPDataset(KEYPOINTS_FOLDER_TEST, transform=None, demo=False)

data_loader_train = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn)
data_loader_val = DataLoader(dataset_val, batch_size=1, shuffle=False, collate_fn=collate_fn)
data_loader_test = DataLoader(dataset_test, batch_size=1, shuffle=False, collate_fn=collate_fn)

start_time = time.time()
for epoch in range(num_epochs):
    model.train()
    total_loss = 0

    for imgs, target_dicts, _ in data_loader_train:
        imgs = [img.to(device) for img in imgs]
        optimizer.zero_grad()
        
        with autocast():
            KGNN2D, original_graphs, placeholder_masks = model(imgs)            
            keypoints_gt = process_batch_keypoints(target_dicts)
            print("Ground truth keypoints", keypoints_gt)
            reordered_normalized_keypoints = reorder_batch_keypoints(KGNN2D)
            denormalized_keypoints = denormalize_keypoints(reordered_normalized_keypoints)
            print("Final precicted keypoints", denormalized_keypoints)
            gt_distances_angles = calculate_gt_distances_angles(keypoints_gt)
            pred_distances_angles = calculate_gt_distances_angles(denormalized_keypoints)
            loss_kgnn2d = kgnn2d_loss(keypoints_gt, denormalized_keypoints, gt_distances_angles[:, :, 0], 
                                      gt_distances_angles[:, :, 1], gt_distances_angles[:, :, 2], 
                                      gt_distances_angles[:, :, 3], pred_distances_angles[:, :, 0], 
                                      pred_distances_angles[:, :, 1], pred_distances_angles[:, :, 2], 
                                      pred_distances_angles[:, :, 3], original_graphs, KGNN2D, placeholder_masks)
            print("loss per item ", loss_kgnn2d)
            
        scaler.scale(loss_kgnn2d).backward()
        scaler.step(optimizer)
        scaler.update()
        total_loss += loss_kgnn2d.item()
    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {total_loss / len(data_loader_train)}')
    
end_time = time.time()

total_time = end_time - start_time
print("total time", total_time)
        

            

Copying files: 49670 files [00:03, 13489.20 files/s]


initial predicted keypoints tensor([[2.5000e+02, 4.4100e+02, 1.0000e+00, 1.0000e+00],
        [2.5200e+02, 3.1100e+02, 1.0000e+00, 2.0000e+00],
        [2.6000e+02, 2.5200e+02, 1.0000e+00, 3.0000e+00],
        [2.6400e+02, 1.9300e+02, 9.9986e-01, 4.0000e+00],
        [2.9800e+02, 1.9900e+02, 9.9797e-01, 5.0000e+00],
        [3.4300e+02, 2.5600e+02, 9.9976e-01, 6.0000e+00],
        [3.9000e+02, 3.1400e+02, 9.9942e-01, 7.0000e+00],
        [4.2800e+02, 3.1600e+02, 1.3652e-01, 8.0000e+00],
        [4.2000e+02, 3.6300e+02, 9.9640e-01, 9.0000e+00]], device='cuda:0')
filled missing keypoints [[250.0, 441.0, 1.0, 1.0], [252.0, 311.0, 0.999998927116394, 2.0], [260.0, 252.0, 0.999995231628418, 3.0], [264.0, 193.0, 0.9998558759689331, 4.0], [298.0, 199.0, 0.9979718327522278, 5.0], [343.0, 256.0, 0.9997555613517761, 6.0], [390.0, 314.0, 0.9994248151779175, 7.0], [428.0, 316.0, 0.13651642203330994, 8.0], [420.0, 363.0, 0.9964007139205933, 9.0]]
Data(x=[9, 8], edge_index=[2, 18]) tensor([False, Fal

/tmp/ipykernel_78284/1660099778.py:4: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  dx, dy = torch.tensor(dx).to(device), torch.tensor(dy).to(device)


initial predicted keypoints tensor([[250.0000, 442.0000,   1.0000,   1.0000],
        [252.0000, 312.0000,   1.0000,   2.0000],
        [267.0000, 254.0000,   1.0000,   3.0000],
        [282.0000, 196.0000,   1.0000,   4.0000],
        [312.0000, 203.0000,   1.0000,   5.0000],
        [437.0000, 289.0000,   1.0000,   7.0000],
        [431.0000, 323.0000,   0.9989,   8.0000],
        [389.0000, 316.0000,   0.9987,   9.0000]], device='cuda:0')
Previous Kp tensor([312.0000, 203.0000,   1.0000,   5.0000], device='cuda:0')
Next Kp tensor([437.0000, 289.0000,   1.0000,   7.0000], device='cuda:0')
Filled missing keypoint for label 6 at position (374.5, 246.0)
filled missing keypoints [[250.0, 442.0, 1.0, 1.0], [252.0, 312.0, 0.9999992847442627, 2.0], [267.0, 254.0, 0.9999815225601196, 3.0], [282.0, 196.0, 0.9999986886978149, 4.0], [312.0, 203.0, 0.9999982118606567, 5.0], [tensor(374.5000, device='cuda:0'), tensor(246., device='cuda:0'), 0, 6], [437.0, 289.0, 0.9999760389328003, 7.0], [431.0, 

Ground truth keypoints tensor([[[250.5689, 442.3043],
         [252.5741, 311.8228],
         [241.8606, 253.7019],
         [231.1472, 195.5810],
         [261.0211, 189.0741],
         [331.5433, 165.4438],
         [402.0656, 141.8135],
         [416.2184, 171.5165],
         [379.0897, 189.2074]]], device='cuda:0')
Final precicted keypoints tensor([[[411.8229, 238.4351],
         [418.5677, 262.0190],
         [411.8750, 259.2847],
         [380.3450, 302.6855],
         [344.9666, 309.2578],
         [358.3521, 328.4375],
         [401.9132, 310.5664],
         [430.5469, 280.4102],
         [423.8542, 263.9648]]], device='cuda:0', grad_fn=<StackBackward0>)
loss per item  tensor(32819.9023, device='cuda:0', grad_fn=<AddBackward0>)
initial predicted keypoints tensor([[2.5000e+02, 4.4200e+02, 1.0000e+00, 1.0000e+00],
        [2.5200e+02, 3.1200e+02, 1.0000e+00, 2.0000e+00],
        [1.9900e+02, 2.8700e+02, 1.0000e+00, 3.0000e+00],
        [1.4300e+02, 2.6200e+02, 9.9999e-01, 4.0000e

...

Final precicted keypoints tensor([[[320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [205.5535, 209.6971],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000]]], device='cuda:0', grad_fn=<StackBackward0>)
loss per item  tensor(48891.3281, device='cuda:0', grad_fn=<AddBackward0>)
initial predicted keypoints tensor([[2.5000e+02, 4.4200e+02, 1.0000e+00, 1.0000e+00],
        [2.5300e+02, 3.1100e+02, 1.0000e+00, 2.0000e+00],
        [2.8000e+02, 2.6000e+02, 9.9998e-01, 3.0000e+00],
        [3.1600e+02, 2.1000e+02, 9.9994e-01, 4.0000e+00],
        [3.4700e+02, 2.2600e+02, 9.9976e-01, 5.0000e+00],
        [4.1900e+02, 2.2000e+02, 9.9997e-01, 6.0000e+00],
        [4.9600e+02, 2.1300e+02, 9.9998e-01, 7.0000e+00],
        [5.3300e+02, 2.1200e+02, 7.3039e-02, 8.0000e+00],
        [5.3100e+02, 2.5600e+02, 9.7121e-01, 9.0000e+00]], device='cuda:0')
filled 

initial predicted keypoints tensor([[250.0000, 442.0000,   1.0000,   1.0000],
        [253.0000, 311.0000,   1.0000,   2.0000],
        [280.0000, 261.0000,   1.0000,   3.0000],
        [317.0000, 210.0000,   1.0000,   4.0000],
        [343.0000, 225.0000,   1.0000,   5.0000],
        [479.0000, 294.0000,   0.9999,   7.0000],
        [516.0000, 290.0000,   0.9991,   8.0000],
        [522.0000, 335.0000,   0.9958,   9.0000]], device='cuda:0')
Previous Kp tensor([343.0000, 225.0000,   1.0000,   5.0000], device='cuda:0')
Next Kp tensor([479.0000, 294.0000,   0.9999,   7.0000], device='cuda:0')
Filled missing keypoint for label 6 at position (411.0, 259.5)
filled missing keypoints [[250.0, 442.0, 1.0, 1.0], [253.0, 311.0, 0.9999992847442627, 2.0], [280.0, 261.0, 0.9999843835830688, 3.0], [317.0, 210.0, 0.9999897480010986, 4.0], [343.0, 225.0, 0.9999583959579468, 5.0], [tensor(411., device='cuda:0'), tensor(259.5000, device='cuda:0'), 0, 6], [479.0, 294.0, 0.9999128580093384, 7.0], [516.0, 

Final precicted keypoints tensor([[[320.0000, 240.0000],
         [320.0000, 240.0000],
         [258.4887, 236.3754],
         [246.6528, 227.6913],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000]]], device='cuda:0', grad_fn=<StackBackward0>)
loss per item  tensor(49862.3555, device='cuda:0', grad_fn=<AddBackward0>)
initial predicted keypoints tensor([[2.5100e+02, 4.4300e+02, 1.6269e-01, 1.0000e+00],
        [2.4800e+02, 3.1100e+02, 1.0000e+00, 2.0000e+00],
        [2.9400e+02, 2.6700e+02, 9.9999e-01, 3.0000e+00],
        [3.3500e+02, 2.2300e+02, 9.9999e-01, 4.0000e+00],
        [3.5800e+02, 2.4400e+02, 9.9998e-01, 5.0000e+00],
        [4.2600e+02, 2.1000e+02, 9.9997e-01, 6.0000e+00],
        [4.9100e+02, 1.7500e+02, 9.9883e-01, 7.0000e+00],
        [4.7000e+02, 2.3200e+02, 9.5707e-01, 9.0000e+00]], device='cuda:0')
Previous Kp tensor([491.0000, 175.0000,   0.9988,   7.0000], devi

Ground truth keypoints tensor([[[250.5689, 442.3043],
         [252.5741, 311.8228],
         [277.8832, 257.4452],
         [303.1924, 203.0676],
         [331.4742, 215.5991],
         [407.2696, 215.5315],
         [483.0650, 215.4639],
         [510.5575, 236.6222],
         [484.1096, 270.9877]]], device='cuda:0')
Final precicted keypoints tensor([[[320.0000, 240.0000],
         [320.0000, 240.0000],
         [290.1360, 234.5335],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000],
         [320.0000, 240.0000]]], device='cuda:0', grad_fn=<StackBackward0>)
loss per item  tensor(35063.9336, device='cuda:0', grad_fn=<AddBackward0>)


KeyboardInterrupt: 